# 第14週 社群網路分析

**Author** : 蔡俊宏

**Date created** : 2023/05/14

本週課程利用之前使用的PTT美食版，觀察發文者與回文者的情況

In [1]:
! pip install pyvis networkx pandas numpy

In [2]:
import pandas as pd
import numpy as np
import pyvis
import networkx as nx
import IPython

In [3]:
raw_data = pd.read_csv('./raw_data/buffet_20_22.csv')
raw_data = raw_data[raw_data.artComment != '[]']
raw_data = raw_data.sample(round(raw_data.shape[0]/4))
print(raw_data.shape)
raw_data.head()


(123, 11)


system_id                                             artUrl   
394         395  https://www.ptt.cc/bbs/Food/M.1596626709.A.48F...  \
303         304  https://www.ptt.cc/bbs/Food/M.1592063279.A.E0E...   
239         240  https://www.ptt.cc/bbs/Food/M.1589791255.A.49C...   
1231       1232  https://www.ptt.cc/bbs/Food/M.1643432020.A.8B5...   
854         855  https://www.ptt.cc/bbs/Food/M.1616237558.A.40E...   

                     artTitle              artDate   artPoster artCatagory   
394             [食記]高雄小反推花福韓燒  2020-08-05 19:25:04      linche        Food  \
303           [食記]台北欣葉日本料理健康店  2020-06-13 23:47:57     nikcoke        Food   
239     [食記]新北板橋鍋飽飽火鍋＄145起吃超飽  2020-05-18 16:40:52     ally701        Food   
1231            [食記]台中陶樂里庭園蔬食  2022-01-29 12:53:37        dass        Food   
854   [食記]台北中正北車泰獅泰式料理(月亮蝦餅超厚  2021-03-20 18:52:32  TW00500203        Food   

                                             artContent   
394   餐廳名稱：花福韓燒\n   消費時間：2020/5\n   地址：807高雄市三民區正忠路4...  \
303   日式料理吃到飽系列之--欣葉日本料理健康店\n\n有圖有真相圖文並茂版：\nhttps://...   
239   2019年5月\n無音樂。有圖真相網誌好讀版\nhttps://ally701.pixnet...   
1231  餐廳名稱：陶樂里庭園蔬食\n   消費時間：2022年/1月\n   地址：台中市潭子區豐興...   
854   【泰獅 泰式料理】\n電話：02 2311 7778\n地址：台北市中正區武昌街一段16巷1...   

                                             artComment            e_ip   
394   [{"cmtStatus": "推", "cmtPoster": "faway", "cmt...  27.246.197.217  \
303   [{"cmtStatus": "推", "cmtPoster": "perfectperfe...  211.75.180.193   
239   [{"cmtStatus": "推", "cmtPoster": "allen1224a",...    101.10.19.36   
1231  [{"cmtStatus": "推", "cmtPoster": "King12man36"...  123.110.12.146   
854   [{"cmtStatus": "推", "cmtPoster": "ring0816", "...  49.216.222.250   

             insertedDate dataSource  
394   2020-08-06 00:31:00        ptt  
303   2020-06-14 00:04:36        ptt  
239   2020-05-19 00:04:19        ptt  
1231  2022-01-30 00:13:52        ptt  
854   2021-03-21 00:29:02        ptt

In [4]:
#parse comment

def getComtInfo(com):
  cmters,cmt_statuss = [],[]
  com = eval(com)
  for i in com:
    print(i)
    cmters.append(i['cmtPoster'])
    cmt_statuss.append(i['cmtStatus'])
  return pd.Series([cmters, cmt_statuss])

raw_data[['artComter','artStatus']] = raw_data['artComment'].apply(lambda r: getComtInfo(r))

{'cmtStatus': '推', 'cmtPoster': 'faway', 'cmtContent': ':他們當務之急要改善的是抽氣設備,現在的效果簡直趨近於零', 'cmtDate': '2020-08-06 08:15:00'}
{'cmtStatus': '→', 'cmtPoster': 'linche', 'cmtContent': ':我覺得需要好好整間重新整頓0..0', 'cmtDate': '2020-08-06 20:36:00'}
{'cmtStatus': '推', 'cmtPoster': 'perfectperfe', 'cmtContent': ':現在加欣葉line好友，會有送滿500可折100的優待券', 'cmtDate': '2020-06-14 10:34:00'}
{'cmtStatus': '→', 'cmtPoster': 'perfectperfe', 'cmtContent': ':。', 'cmtDate': '2020-06-14 10:34:00'}
{'cmtStatus': '推', 'cmtPoster': 'allen1224a', 'cmtContent': ':2019，5月？', 'cmtDate': '2020-05-19 23:31:00'}
{'cmtStatus': '推', 'cmtPoster': 'King12man36', 'cmtContent': ':推', 'cmtDate': '2022-01-29 13:17:00'}
{'cmtStatus': '推', 'cmtPoster': 'ring0816', 'cmtContent': ':饗泰多的月亮蝦餅也超厚~', 'cmtDate': '2021-03-21 21:07:00'}
{'cmtStatus': '推', 'cmtPoster': 'yakifone', 'cmtContent': ':這名字', 'cmtDate': '2020-09-22 16:12:00'}
{'cmtStatus': '→', 'cmtPoster': 'breeze1006', 'cmtContent': ':之前吃過一次，記憶點很低、油煙味殘留在衣服上散不去', 'cmtDate': '2020-09-22 18:39:

In [5]:
raw_data = raw_data.explode(['artComter','artStatus'])
socail_data = raw_data[['artUrl','artPoster','artComter','artStatus']]
socail_data.head(10)


artUrl   artPoster   
394   https://www.ptt.cc/bbs/Food/M.1596626709.A.48F...      linche  \
394   https://www.ptt.cc/bbs/Food/M.1596626709.A.48F...      linche   
303   https://www.ptt.cc/bbs/Food/M.1592063279.A.E0E...     nikcoke   
303   https://www.ptt.cc/bbs/Food/M.1592063279.A.E0E...     nikcoke   
239   https://www.ptt.cc/bbs/Food/M.1589791255.A.49C...     ally701   
1231  https://www.ptt.cc/bbs/Food/M.1643432020.A.8B5...        dass   
854   https://www.ptt.cc/bbs/Food/M.1616237558.A.40E...  TW00500203   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   

         artComter artStatus  
394          faway         推  
394         linche         →  
303   perfectperfe         推  
303   perfectperfe         →  
239     allen1224a         推  
1231   King12man36         推  
854       ring0816         推  
492       yakifone         推  
492     breeze1006         →  
492   OGCOGCOGCOGC         推

In [6]:
socail_data.artStatus.unique()

array(['推', '→', '噓'], dtype=object)

簡單劃出文章、發文者、評論者的網路

In [7]:
# 建立邊的資料
import random


po_df = socail_data[['artPoster','artUrl']].drop_duplicates().rename(columns = {'artPoster':'src','artUrl':'dis'})
sample_url = random.choices(po_df.dis.unique().tolist(),k=300)
po_df = po_df[po_df.dis.isin(sample_url)]
re_df = socail_data[['artComter','artUrl','artStatus']].rename(columns = {'artComter':'src','artUrl':'dis','artStatus':'weight'})
re_df = re_df[re_df.dis.isin(sample_url)]
re_df = re_df[~re_df['src'].isna()]



def convertStatus(s):
  if s == '推':
    return 2
  elif s == '→':
    return 1
  else :
    return -1
re_df['weight'] = re_df['weight'].map(convertStatus)
re_df = re_df.groupby(['src','dis']).sum().reset_index()

# 設定分數低的為紅色
def getColor(w):
  if w>0:
    return 'green'
  else:
    return 'red'
re_df['color'] = re_df.weight.map(getColor)



In [8]:
re_df

src                                                dis  weight   
0        ALENDA  https://www.ptt.cc/bbs/Food/M.1602012705.A.031...       2  \
1        AlphaD  https://www.ptt.cc/bbs/Food/M.1579766074.A.BB5...       2   
2        AlphaD  https://www.ptt.cc/bbs/Food/M.1583982662.A.755...       2   
3     Alphaplus  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       0   
4        Arutha  https://www.ptt.cc/bbs/Food/M.1587898980.A.623...       7   
..          ...                                                ...     ...   
480  zeroyaking  https://www.ptt.cc/bbs/Food/M.1620371370.A.52C...       1   
481  zeroyaking  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       2   
482    zxc89003  https://www.ptt.cc/bbs/Food/M.1645607596.A.305...       2   
483     zyc5566  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       1   
484    zzz50126  https://www.ptt.cc/bbs/Food/M.1655268051.A.324...       2   

     color  
0    green  
1    green  
2    green  
3      red  
4    green  
..     ...  
480  green  
481  green  
482  green  
483  green  
484  green  

[485 rows x 4 columns]

In [9]:
# 人為綠色節點
# po文為橘色節點

netWork = pyvis.network.Network(notebook=True, cdn_resources='in_line',directed=True)
person = list(set(po_df.src.unique().tolist()+re_df.src.unique().tolist()))
url = po_df.dis.unique().tolist()
netWork.add_nodes(
    nodes = person,
    value = [1 for i in range(len(person))],
    color = ['#66CDAA' for i in range(len(person))],
    title = person
)
netWork.add_nodes(
    nodes = url,
    value = [2 for i in range(len(url))],
    color = ['#FFB366' for i in range(len(url))],
    title = url
)
for i in po_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color='grey')
for i in re_df.to_numpy():
  netWork.add_edge(i[0],i[1],width = 2,color=i[3])

# 設定layout
netWork.repulsion()

# netWork.toggle_physics(True)
# netWork.set_options("""
# const options = {
#   "physics": {
#     "forceAtlas2Based": {
#       "springLength": 100
#     },
#     "minVelocity": 0.75,
#     "solver": "forceAtlas2Based",
#     "timestep": 0.48
#   }
# }
# """)

netWork.show("./basic_netWork.html")
IPython.display.HTML('basic_netWork.html')

./basic_netWork.html


以上可以看出多數的文章留言偏少，只有四篇的文章的回文較多



計算網友之間的關係

In [10]:
pos_cmt = socail_data.copy()
pos_cmt = pos_cmt[~pos_cmt.artComter.isna()]
pos_cmt.head(10)

artUrl   artPoster   
394   https://www.ptt.cc/bbs/Food/M.1596626709.A.48F...      linche  \
394   https://www.ptt.cc/bbs/Food/M.1596626709.A.48F...      linche   
303   https://www.ptt.cc/bbs/Food/M.1592063279.A.E0E...     nikcoke   
303   https://www.ptt.cc/bbs/Food/M.1592063279.A.E0E...     nikcoke   
239   https://www.ptt.cc/bbs/Food/M.1589791255.A.49C...     ally701   
1231  https://www.ptt.cc/bbs/Food/M.1643432020.A.8B5...        dass   
854   https://www.ptt.cc/bbs/Food/M.1616237558.A.40E...  TW00500203   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   
492   https://www.ptt.cc/bbs/Food/M.1600760494.A.41D...       grawd   

         artComter artStatus  
394          faway         推  
394         linche         →  
303   perfectperfe         推  
303   perfectperfe         →  
239     allen1224a         推  
1231   King12man36         推  
854       ring0816         推  
492       yakifone         推  
492     breeze1006         →  
492   OGCOGCOGCOGC         推

In [11]:
pos_cmt['score'] = pos_cmt['artStatus'].apply(lambda r: convertStatus(r))
pos_cmt = pos_cmt.groupby(['artComter','artPoster']).sum('score').reset_index()
pos_cmt = pos_cmt[pos_cmt.score>=0]
pos_cmt = pos_cmt[pos_cmt.artComter != pos_cmt.artPoster]
# pos_cmt.score = 1
pos_cmt

artComter     artPoster  score
0        ALENDA     chickenbo      2
2        AlphaD  gillianshine      2
3     Alphaplus       reesion      0
4        Arutha       NouTsan      7
5           BUE     cheauwong      4
..          ...           ...    ...
494     yzkg391         oao88      2
495  zeroyaking       reesion      3
496    zxc89003        adai69      2
497     zyc5566       reesion      1
498    zzz50126       reesion      2

[471 rows x 3 columns]

In [12]:
pers = np.unique(pos_cmt[['artComter', 'artPoster']])
mat = pd.pivot_table(pos_cmt,index = 'artComter', columns = 'artPoster' ,values='score' ).fillna(0)\
  .reindex(columns=pers, index=pers, fill_value=0).to_numpy()
print(mat.shape)
tri = (np.tril(mat,-1).T + np.triu(mat,1))
mat_s = tri+tri.T

# # print((mat == mat.transpose()).all())

# G = nx.DiGraph(mat)
# G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
# G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
# mat = nx.adjacency_matrix(G_max_sub).todense()
# node_idx = list(G_max_sub.nodes)
# # mat = mat[np.ix_(node_idx,node_idx)]
# pers = pers[node_idx]
# print((mat == mat.transpose()).all())

# # 計算無向圖的adj


(505, 505)


In [13]:
def random_color():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(),r(),r())

def matPresentGraph(mat:np.array,node_id:list,node_type:list=None,node_value:list = None,directed = True,edge_color=None) -> pyvis.network.Network:

  if directed != True:
    if (mat == mat.transpose()).all():
      print('matrix is Symmetric')
    else:
      print('matrix is not Symmetric')
  if node_type == None:
    c = random_color()
    node_colors = [c for i in range(len(node_id))]
    node_type = [" " for i in range(len(node_id))]
  else:
    node_color_map = {}
    for i in set(node_type):
      while True:
        c = random_color()
        if c not in node_color_map.values():
          break
      node_color_map[i] = c
    node_colors = [node_color_map[i] for i in node_type]
  # print(node_colors)
  if edge_color == None:
    edge_color = random_color()
  edge_color = random_color()
  if node_value == None:
    node_value = [1 for i in range(len(node_id))]

  net = pyvis.network.Network(notebook=True, directed = directed, cdn_resources='in_line')
  
  titles_list = []
  for i ,j in zip(node_id,node_type):
    titles_list.append(str(i)+":"+str(j))

  net.add_nodes(
      nodes = node_id,
      value = node_value,
      label = node_id,
      title = titles_list,
      color = node_colors
  )

  for row in range(len(node_id)):
    for col in range(len(node_id)):
      if mat[row][col]>0.:
        net.add_edge(
            node_id[row],node_id[col],width = mat[row][col],color = edge_color,title = mat[row][col]
        )
  net.repulsion()
  return net


In [14]:
# 定義發文者（po）、評論者(cmt)、兩者兼具(both)
node_type = []

cmt_list = pos_cmt['artComter'].unique().tolist()
po_list = pos_cmt['artPoster'].unique().tolist()
both_list = list(set(cmt_list) & set(po_list))
for p in pers:
  if p in both_list:
    node_type.append('both')

  elif p in cmt_list:
    node_type.append('cmt')

  elif p in po_list:
    node_type.append('po')



In [15]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type)
net.show("./pers_netWork.html")
IPython.display.HTML('pers_netWork.html')

./pers_netWork.html


計算eigenvector centrality （無向圖）

In [16]:

eigenvec = np.array(list(nx.eigenvector_centrality(nx.Graph(mat_s),max_iter = 10000).values()))
eigenvec = (eigenvec-np.min(eigenvec))/(np.max(eigenvec)-np.min(eigenvec))


In [17]:
q = np.quantile(eigenvec,[.2,.4,.6,.8])
q

array([6.69500552e-33, 1.22880427e-15, 2.23944918e-13, 9.62255870e-02])

In [18]:
node_value = []


for i in eigenvec:

  if i > q[3]:
    node_value.append(25)
  elif i >q[2]:
    node_value.append(20)
  elif i>q[1]:
    node_value.append(15)
  elif i>q[0]:
    node_value.append(10)
  else:
    node_value.append(5)
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value = node_value,directed=False)
net.show("./pers_eig_netWork.html")
IPython.display.HTML('pers_eig_netWork.html')


matrix is not Symmetric
./pers_eig_netWork.html


我們可以發現有多次評論的人，或是評論的文章同時有多人評論的，重要程度愈高

PageRank (有向圖)

In [19]:
# Digraph 設定有向圖
pagerank = np.array(list(nx.pagerank(nx.DiGraph(mat)).values()))
# pagerank = (pagerank-np.min(pagerank))/(np.max(pagerank)-np.min(pagerank))
pagerank

array([0.00113836, 0.00355845, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.0021064 , 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00404247,
       0.00404247, 0.0021064 , 0.00113836, 0.00113836, 0.00113836,
       0.0050105 , 0.00113836, 0.00113836, 0.00113836, 0.0021064 ,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113836,
       0.0021064 , 0.00113836, 0.00113836, 0.00326804, 0.00113836,
       0.00113836, 0.0021064 , 0.0050105 , 0.00903927, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00876028, 0.00113836, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00636575, 0.00113836, 0.00113836,
       0.00113836, 0.00113836, 0.00113836, 0.00113836, 0.00113

In [20]:
net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=(pagerank*1000).tolist())
net.show("./pers_page_netWork.html")
IPython.display.HTML('pers_page_netWork.html')


./pers_page_netWork.html


可以看出indegree 較多，重要程度愈高

Hits score （有向圖）

In [21]:
out_,in_ = nx.hits(nx.DiGraph(mat),max_iter=100)
out_,in_ = np.array(list(out_.values())),np.array(list(in_.values()))
out_ = (out_-np.min(out_))/(np.max(out_)-np.min(out_))
in_ = (in_-np.min(in_))/(np.max(in_)-np.min(in_))


In [22]:
in_q = np.quantile(in_,[.2,.4,.6,.8])
out_q = np.quantile(out_,[.2,.4,.6,.8])


In [23]:
in_q

array([4.04120020e-16, 4.07480062e-16, 4.09020356e-16, 4.13165099e-16])

In [24]:
node_value = []


for i in out_:
  if i > out_q[3]:
    node_value.append(25)
  elif i >out_q[2]:
    node_value.append(20)
  elif i>out_q[1]:
    node_value.append(15)
  elif i>out_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_out_netWork.html")
IPython.display.HTML('pers_out_netWork.html')

./pers_out_netWork.html


In [25]:
node_value = []
for i in in_:
  if i > in_q[3]:
    node_value.append(25)
  elif i >in_q[2]:
    node_value.append(20)
  elif i>in_q[1]:
    node_value.append(15)
  elif i>in_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_in_netWork.html")
IPython.display.HTML('pers_in_netWork.html')

./pers_in_netWork.html


可以發現indegree/outdegree的多寡會決定其重要程度

betweenness centrality

In [26]:
bet = np.array(list(nx.betweenness_centrality(nx.Graph(mat_s)).values()))
bet = (bet-np.min(bet))/(np.max(bet)-np.min(bet))
bet_q = np.quantile(bet,[.2,.4,.6,.8])

In [27]:
node_value = []
for i in bet:
  if i > bet_q[3]:
    node_value.append(25)
  elif i > bet_q[2]:
    node_value.append(20)
  elif i>bet_q[1]:
    node_value.append(15)
  elif i>bet_q[0]:
    node_value.append(10)
  else:
    node_value.append(5)

net = matPresentGraph(mat = mat,node_id = pers,node_type = node_type,node_value=node_value)
net.show("./pers_bet_netWork.html")
IPython.display.HTML('pers_bet_netWork.html')

./pers_bet_netWork.html


Transitivity/Density/Distance/Diameter/Clustering

計算最大的subgraph 的 measure

In [28]:
# 計算max subgraph
G = nx.Graph(mat_s)
G_sub = sorted(nx.connected_components(G), key=len, reverse=True)
G_max_sub = G.subgraph(G_sub[0])
# # 重新定義 mat
sub_mat = nx.adjacency_matrix(G_max_sub).todense()
node_idx = list(G_max_sub.nodes)
sub_pers = pers[node_idx]


畫出最大subgraph

In [29]:
net = matPresentGraph(mat=sub_mat,node_id=sub_pers,directed=False)
net.show("./max_sub.html")
IPython.display.HTML('max_sub.html')

matrix is Symmetric
./max_sub.html


計算transitivity

In [30]:
nx.transitivity(nx.Graph(sub_mat))

0.0037998733375554147

計算density 及 distance

In [31]:
nx.density(nx.Graph(sub_mat))

0.009291803013776108

In [32]:
nx.average_shortest_path_length(nx.Graph(sub_mat))

6.714782046620612

計算diameter

In [33]:
nx.diameter(nx.Graph(sub_mat))

15

計算clustering

In [34]:
nx.average_clustering(nx.Graph(sub_mat))

0.007630112787063458